In [0]:
!pip install langdetect
!pip install nltk
!pip install pyspellchecker

     |████████████████████████████████| 981 kB 5.6 MB/s 
  Created wheel for langdetect: filename=langdetect-1.0.9-py3-none-any.whl size=993242 sha256=ac4333b053c5b377ec45f6ac8ad6d583e4775ed115682a2b6093a5de48db5933
  Stored in directory: /root/.cache/pip/wheels/d1/c1/d9/7e068de779d863bc8f8fc9467d85e25cfe47fa5051fff1a1bb
Successfully built langdetect
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-d87afbc2-c62e-4509-8d35-2071dd7dafd2/bin/python -m pip install --upgrade pip' command.
     |████████████████████████████████| 1.5 MB 5.2 MB/s 
     |████████████████████████████████| 77 kB 3.5 MB/s 
     |████████████████████████████████| 768 kB 12.3 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-d87afbc2-c62e-4509-8d35-2071dd7dafd2/bin/python -m pip install --upgrade pip' command.
     |████████████████████████████████| 2.5 MB 5.1 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv

In [0]:
from pyspark.sql.functions import *
from nltk.stem import SnowballStemmer
from spellchecker import SpellChecker
from langdetect import detect
import nltk
import re
import string
from pyspark.sql.types import ArrayType, IntegerType, StringType, DoubleType
nltk.download('stopwords')
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from spellchecker import SpellChecker
from pyspark.ml.feature import HashingTF, IDF
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.mllib.evaluation import MulticlassMetrics

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [0]:
def csv_to_df(filename):
    """has one argument which expects a csv filename.
       This function loads the data in the file into 
       a dataframe and then displays the dataframe"""
    # File location and type
    file_location = "/FileStore/tables/" + filename
    file_type = "csv"
    # CSV options
    infer_schema = "true"
    first_row_is_header = "true"
    delimiter = ","
    # The applied options are for CSV files. For other file types, these will be ignored.
    df = spark.read.format(file_type) \
         .option("inferSchema", infer_schema) \
         .option("header", first_row_is_header) \
         .option("sep", delimiter) \
         .option("multiline","True") \
         .option("escape","\"") \
         .load(file_location)
    return df

Step 1: Send our labelled sentimental data to be preprocessed

In [0]:
df_labeled_reviews = csv_to_df("laballed_review_final.csv")
display(df_labeled_reviews)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment 44799007 664856750 2020 366313419 Nick This place is top notch . Very clean place to stay and excellent location. 2 44799007 664874365 2020 341666414 Anthony The place isn’t bad , they just have some plumbing issues that need to be worked on 1 44799007 666278215 2020 74495895 Elizabeth Sonders was such a beautiful space with an amazing view! Would definitely stay there again, the location was perfect, easy train ride to Times Square! 2 44799007 666306913 2020 212875697 Jonathan Great place to stay! I highly recommend!! 2 44799007 666333507 2020 346697349 Devante Very clean and stylish. 2 44799007 666353541 2020 78949597 Esther I absolutely loved it! Beautiful place, very clean. 1 44799007 666425016 2020 89762643 Diemeary I never post this detailed of a review but I feel this one is important to hit key points. This specific Airbnb is a great deal, great stay, amazing views, and very clean and nice. Although the Airbnb is attached to a partnering company Sonder, the Sonder process was not the same value as I am used to with Airbnb. You have to call the Sonder phone number directly and do everything practically outside of Airbnb. The check-in instructions never came but stated they would three days prior after completing the covid health questionnaire and sending confirmation which I did via email with a screenshot as requested, even after calling a day before stay to confirm the door access code downstairs and at the physical door upon check-in there was still a marked missed as no one had a clear answer as to where the codes to seem to be/how to retrieve them (odd) and to wait until the morning to receive final codes due to a "technical" issue that is "in process". Well, the morning came, and nothing was ever received but I was busy running around. I didn't freak out or anything like that because I was told a Sonder representative would be available on site. I arrive to the apartment style/hotel style location and the front security has no idea about check-ins and tells me she does not work with check-in and is with a third party company and knows nothing about Sonder staff on site. Of course this did not help my situation, so I called the Sonder number, again, to try to come to a resolution to get checked in, and the wait time was probably about 20 minutes until the same security calls me and points at a man who she says she believes is a supervisor on site with Sonder. All while this was happening, a man came in with a similar situation to mine. I flagged the representative down, and he helped me, if it hadn't been for him I would imagine waiting 30 minutes to an hour on the phone trying to figure the "technical" issue. He was unable to give a door code for either downstairs or my room but had the master key to at least let me in. This was a step in the right direction but still a headache having to call later to escalate my issue because I had a guest arriving later and I was not going to be at the stay at the time of their arrival so I needed to give the codes to enter the stay, the codes in which at that point I myself didn't even have. I will say Sonder did allow me to check-in early after it was approved but the whole check-in process was a blur and no one seemed to be on the same page which sucked because it ruined my first initial experience of an awesome stay. I would definitely say there is education and fixings needed in place to better fix issues like this between Sonder and Airbnb for the experience for the guest(s). The only other issue we had was our Wifi on and off working and this was only an issue primarily because the Wifi helped using the TV. The process in getting the Wifi also took about two days. It seems the turn around time to get a response is 24 hours writing Sonder on the Airbnb portal and hit or miss on the Sonder customer service line but who wants to spend all day on the phone on their trip. We eventually learned you can te

In [0]:
@udf(returnType=ArrayType(StringType()))
def preprocess_text(sentence):
    words = word_tokenize(sentence)
    sw = set(stopwords.words("english"))
    words = [word for word in words if word not in sw]
    # b. Remove punctuation marks
    punctuation = set(string.punctuation)
    words = [word for word in words if word not in punctuation]
    # c. Remove non-alphabetic words
    words = [word for word in words if word.isalpha()]
    # d. Checking and fix the spelling of the word
    spell = SpellChecker()
    misspelled = spell.unknown(words)
    new_words = []
    for word in words:
        if word in misspelled:
            corrected = spell.correction(word)
            if corrected:
                new_words.append(corrected)
        else:
            new_words.append(word)
    
    # e. Use SnowBallStemmer to stem each word
    snowball = SnowballStemmer(language = 'english')
    stemmed_words = [snowball.stem(word) for word in new_words]

    return words

In [0]:
df_processed = df_labeled_reviews.withColumn('processed_text', preprocess_text(df_labeled_reviews['comments']))
display(df_processed)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text 44799007 664856750 2020 366313419 Nick This place is top notch . Very clean place to stay and excellent location. 2 List(This, place, top, notch, Very, clean, place, stay, excellent, location) 44799007 664874365 2020 341666414 Anthony The place isn’t bad , they just have some plumbing issues that need to be worked on 1 List(The, place, bad, plumbing, issues, need, worked) 44799007 666278215 2020 74495895 Elizabeth Sonders was such a beautiful space with an amazing view! Would definitely stay there again, the location was perfect, easy train ride to Times Square! 2 List(Sonders, beautiful, space, amazing, view, Would, definitely, stay, location, perfect, easy, train, ride, Times, Square) 44799007 666306913 2020 212875697 Jonathan Great place to stay! I highly recommend!! 2 List(Great, place, stay, I, highly, recommend) 44799007 666333507 2020 346697349 Devante Very clean and stylish. 2 List(Very, clean, stylish) 44799007 666353541 2020 78949597 Esther I absolutely loved it! Beautiful place, very clean. 1 List(I, absolutely, loved, Beautiful, place, clean) 44799007 666425016 2020 89762643 Diemeary I never post this detailed of a review but I feel this one is important to hit key points. This specific Airbnb is a great deal, great stay, amazing views, and very clean and nice. Although the Airbnb is attached to a partnering company Sonder, the Sonder process was not the same value as I am used to with Airbnb. You have to call the Sonder phone number directly and do everything practically outside of Airbnb. The check-in instructions never came but stated they would three days prior after completing the covid health questionnaire and sending confirmation which I did via email with a screenshot as requested, even after calling a day before stay to confirm the door access code downstairs and at the physical door upon check-in there was still a marked missed as no one had a clear answer as to where the codes to seem to be/how to retrieve them (odd) and to wait until the morning to receive final codes due to a "technical" issue that is "in process". Well, the morning came, and nothing was ever received but I was busy running around. I didn't freak out or anything like that because I was told a Sonder representative would be available on site. I arrive to the apartment style/hotel style location and the front security has no idea about check-ins and tells me she does not work with check-in and is with a third party company and knows nothing about Sonder staff on site. Of course this did not help my situation, so I called the Sonder number, again, to try to come to a resolution to get checked in, and the wait time was probably about 20 minutes until the same security calls me and points at a man who she says she believes is a supervisor on site with Sonder. All while this was happening, a man came in with a similar situation to mine. I flagged the representative down, and he helped me, if it hadn't been for him I would imagine waiting 30 minutes to an hour on the phone trying to figure the "technical" issue. He was unable to give a door code for either downstairs or my room but had the master key to at least let me in. This was a step in the right direction but still a headache having to call later to escalate my issue because I had a guest arriving later and I was not going to be at the stay at the time of their arrival so I needed to give the codes to enter the stay, the codes in which at that point I myself didn't even have. I will say Sonder did allow me to check-in early after it was approved but the whole check-in process was a blur and no one seemed to be on the same page which sucked because it ruined my first initial experience of an awesome stay. I would definitely say there is education and fixings needed in place to better fix issues like this between Sonder and Airbnb for the experience for the guest(s). The only other issue we had was our

In [0]:
df_processed_count = df_processed.groupby("labelled_sentiment").count()
display(df_processed_count)

labelled_sentiment count 1 71 2 886 0 43

In [0]:
positive_count = df_processed_count.filter(df_processed_count["labelled_sentiment"] == 2).collect()[0]["count"]
neutral_count = df_processed_count.filter(df_processed_count["labelled_sentiment"] == 1).collect()[0]["count"]
negative_count = df_processed_count.filter(df_processed_count["labelled_sentiment"] == 0).collect()[0]["count"]

print("Positive count: ", positive_count)
print("Neutral count: ", neutral_count)
print("Negative count: ", negative_count)

Positive count:  886
Neutral count:  71
Negative count:  43


Step 2: Generate vector column (hashingTF) to create sentiment ml model

In [0]:
hashTF = HashingTF(inputCol="processed_text", outputCol="features")
df_processed_with_hash = hashTF.transform(df_processed)

In [0]:
idf = IDF(inputCol="features", outputCol="idf_features").fit(df_processed_with_hash)
tfidf = idf.transform(df_processed_with_hash)

In [0]:
(training, testing) = df_processed_with_hash.randomSplit([0.7, 0.3])
# print("Training rows: ", training.count(), "| Testing rows: ", testing.count())

In [0]:
(training_tfidf, testing_tfidf) = tfidf.randomSplit([0.7, 0.3])

#Random Forest Classifier Model for LABELLED sentiment

In [0]:
#Training the RandomForestClassifier model

# Train a RandomForest model.
rf = RandomForestClassifier(labelCol="labelled_sentiment", featuresCol="features", numTrees=10)

model = rf.fit(training)

predictions_rf = model.transform(testing)
display(predictions_rf)


listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text features rawPrediction probability prediction 1217318 5355514 2013 6907575 Lara Martin and his housemate were super friendly. I was hardly around the house as I had some friends staying nearby but when I was it was a great place to unwind. Perhaps I can put it down to jetlag and being exhausted but the bed was excellent! Also the room is nicely decorated and the big windows overlooking the street and apartment block opposite were pleasant. I would recommend this place for sure! 2 List(Martin, housemate, super, friendly, I, hardly, around, house, I, friends, staying, nearby, I, great, place, unwind, Perhaps, I, put, jetlag, exhausted, bed, excellent, Also, room, nicely, decorated, big, windows, overlooking, street, apartment, block, opposite, pleasant, I, would, recommend, place, sure) Map(vectorType -> sparse, length -> 262144, indices -> List(13020, 21641, 32680, 33960, 58339, 67994, 68228, 70292, 70998, 77751, 78745, 81686, 96644, 99892, 120328, 129458, 130047, 134125, 137855, 148003, 156204, 164686, 167677, 172888, 176835, 190609, 211084, 211756, 216438, 218825, 224493, 228685, 240900, 254661, 261870), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 5.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 3, values -> List(0.41722972765767197, 0.7783450995293609, 8.804425172812968)) Map(vectorType -> dense, length -> 3, values -> List(0.0417229727657672, 0.07783450995293609, 0.8804425172812967)) 2.0 1217318 5869160 2013 6819922 Jacob Anne and I had a very nice stay at the appartment. We didn't see much of Martin because he was busy working. Roman is also very kind and took good care of us. We even got invited to the Wednesday evening roof-top hangout with friends. Both Martin and Roman gave great advice on the shops and restaurants in the area. It was crazy hot the week we stayed (100 deg) and we are grateful that Martin rushed out and bought and AC on the day we arrived. We would have suffered terribly without it. Thanks! The appartment is nice and in a good location. 10 minutes walk to Bedford st and 5 minutes to the supermarket and the subway. Our room was clean and had a closet with hangers and a dresser for our stuff. The fresh flowers in the room was a nice touch. The rest of the appartment is nice and cosy, but not super clean. It was not a problem though. The appartment is on the top floor, so be able to walk the stairs. The view from the roof is amazing! Thanks for hosting us. 2 List(Anne, I, nice, stay, appartment, We, see, much, Martin, busy, working, Roman, also, kind, took, good, care, us, We, even, got, invited, Wednesday, evening, hangout, friends, Both, Martin, Roman, gave, great, advice, shops, restaurants, It, crazy, hot, week, stayed, deg, grateful, Martin, rushed, bought, AC, day, arrived, We, would, suffered, terribly, without, Thanks, The, appartment, nice, good, location, minutes, walk, Bedford, st, minutes, supermarket, Our, room, clean, closet, hangers, dresser, stuff, The, fresh, flowers, room, nice, touch, The, rest, appartment, nice, cosy, super, clean, It, problem, The, appartment, top, floor, able, walk, stairs, The, view, roof, amazing, Thanks, hosting, us) Map(vectorType -> sparse, length -> 262144, indices -> List(329, 3924, 8538, 9508, 11436, 18176, 22346, 33960, 34752, 43333, 44864, 46411, 47197, 58339, 59007, 64848, 71363, 71450, 73249, 73341, 76764, 77073, 79132, 81210, 84324, 88813, 96104, 101464, 103218, 109156, 109230, 113024, 113432, 120647, 122426, 123343, 130047, 130473, 130740, 131400, 137855, 138627, 141729, 146982, 147136, 155416, 156204, 163145, 164686, 172061, 174207, 174966, 183339, 196946, 198042, 199295, 199468, 201496, 213764, 214859, 216614, 218806, 221843, 222390, 225348, 225898, 230388, 233502, 236715, 242142, 245086, 245743, 249943, 250434, 254061, 254704, 261870)

# WEIGHTED RANDOM FOREST

In [0]:
# Counts - 1000 rows
total_count = positive_count + negative_count + neutral_count

# Weights for 3 classes
c = 3
weight_pos = total_count / (c * positive_count)
weight_neu = total_count / (c * neutral_count)
weight_neg = total_count / (c * negative_count)

In [0]:
# Append the calculated weights to rows with different sentiment labels
df_processed_with_weight = df_processed_with_hash.withColumn("weight", when(col("labelled_sentiment") == 0, weight_neg)
                                                             .when(col("labelled_sentiment") == 1, weight_neu)
                                                             .when(col("labelled_sentiment") == 2, weight_pos))

In [0]:
(training, testing) = df_processed_with_weight.randomSplit([0.7, 0.3])

In [0]:
# Train a RandomForest model.
rfw = RandomForestClassifier(labelCol="labelled_sentiment", featuresCol="features", weightCol="weight", numTrees=20)

model = rfw.fit(training)

predictions = model.transform(testing)
display(predictions)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text features weight rawPrediction probability prediction 1217318 6085380 2013 7353379 Ilaria Simone and I were in Martin's apartment for 6 days during our trip in the US. We didn't see much Martin because he was busy working, but the communication with him has always been excellent and Martin is kind and available. The location is very convenient to visit
 Manhattan, because the subway is 5 minutes walk. 
 The room was ok, however we are used to higher standards of
 cleanliness, mainly in the bathroom. 2 List(Simone, I, Martin, apartment, days, trip, US, We, see, much, Martin, busy, working, communication, always, excellent, Martin, kind, available, The, location, convenient, visit, Manhattan, subway, minutes, walk, The, room, ok, however, used, higher, standards, cleanliness, mainly, bathroom) Map(vectorType -> sparse, length -> 262144, indices -> List(329, 8538, 13020, 23097, 24698, 33960, 41660, 49707, 56781, 56998, 63746, 71450, 73341, 76764, 78745, 79132, 79779, 82515, 118174, 142239, 146982, 156204, 161061, 162250, 164686, 171078, 196815, 197185, 198197, 201496, 204971, 206426, 221843, 245086), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0)) 0.3762227238525207 Map(vectorType -> dense, length -> 3, values -> List(6.378495783598176, 6.447043990344063, 7.1744602260577635)) Map(vectorType -> dense, length -> 3, values -> List(0.31892478917990874, 0.32235219951720306, 0.3587230113028881)) 2.0 1217318 8639549 2013 9194371 Ronan We had a great stay in Williamsburg with Martin and Roman. A nice room, great location, good facilities. Martin and Roman were very friendly, helpful and patient when we had any questions etc... We also got some good tips from them for things to do in the area - we recommend a stay! 2 List(We, great, stay, Williamsburg, Martin, Roman, A, nice, room, great, location, good, facilities, Martin, Roman, friendly, helpful, patient, questions, etc, We, also, got, good, tips, things, area, recommend, stay) Map(vectorType -> sparse, length -> 262144, indices -> List(22346, 33960, 68228, 73249, 73341, 83991, 113432, 130473, 132932, 145697, 146679, 147136, 162055, 164686, 165534, 174582, 207475, 214012, 214676, 221843, 225898, 228685, 261870), values -> List(1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 2.0)) 0.3762227238525207 Map(vectorType -> dense, length -> 3, values -> List(5.718923292899046, 6.8811971068848825, 7.399879600216072)) Map(vectorType -> dense, length -> 3, values -> List(0.28594616464495226, 0.3440598553442441, 0.3699939800108036)) 2.0 3798941 17493706 2014 7755261 Guillaume We stayed in that room for a night and it was really nice. 
 The room is small, but it is furnished with a large and confy confy bed, and the room has a large closet. The temporary AC that was settled is very powerful, so that the room was cool. 
 
 The apartment is really nice and well decorated, especially the living room. 
 
 Thanks Martin for your good advice and for your communicative laughters! We really loved Traif, the tapas restaurant you told us about!! 2 List(We, stayed, room, night, really, nice, The, room, small, furnished, large, confy, confy, bed, room, large, closet, The, temporary, AC, settled, powerful, room, cool, The, apartment, really, nice, well, decorated, especially, living, room, Thanks, Martin, good, advice, communicative, laughters, We, really, loved, Traif, tapas, restaurant, told, us) Map(vectorType -> sparse, length -> 262144, indices -> List(13020, 21641, 22346, 30497, 33358, 33960, 37175, 43084, 52914, 55915, 65568, 71363, 79897, 86703, 96104, 109156, 113432, 148719, 155416, 163145, 164686, 171127, 174207, 186925, 189957, 195763, 201496, 216221, 220270, 221843, 223619, 224493, 224909, 229264, 251904), values -> L

#Evaluations and Metrics for RFC for labelled sentiment. EVALUATING HOW GOOD OUR MODEL WAS

In [0]:
def eval(predictions):
    # Calculate % correct
    correct = predictions.filter(predictions['prediction'] == predictions['labelled_sentiment']).count()
    print("% correct: ", correct/predictions.count())
    
    acc_evaluator = MulticlassClassificationEvaluator(labelCol="labelled_sentiment", predictionCol="prediction", metricName="accuracy")
    accuracy = acc_evaluator.evaluate(predictions)
    print("Accuracy = %g" % (accuracy))
    print("Test Error = %g" % (1.0 - accuracy))
    
    #Now we need to compute the F1 sore
    F1_evaluator = MulticlassClassificationEvaluator(labelCol="labelled_sentiment", predictionCol="prediction", metricName="f1")
    f1_score = F1_evaluator.evaluate(predictions)
    print("F1 Score: ", f1_score)
    

In [0]:
# Compute confusion matrix
def confusion_matrix(predictions):
    predictions = predictions.withColumn("labelled_sentiment", predictions["labelled_sentiment"].cast(DoubleType()))
    predictions = predictions.withColumn("prediction", predictions["prediction"].cast(DoubleType()))
    predictions_and_labels = predictions.select("prediction", "labelled_sentiment").rdd
    metrics = MulticlassMetrics(predictions_and_labels)
    confusion_matrix = metrics.confusionMatrix().toArray()

    print("Confusion Matrix:")
    print(confusion_matrix)
    
    print("Precision for negative: %.3f" % metrics.precision(0.0))
    print("Recall for negative: %.3f" % metrics.recall(0.0))
    print("Precision for neutral: %.3f" % metrics.precision(1.0))
    print("Recall for neutral: %.3f" % metrics.recall(1.0))
    print("Precision for positive: %.3f" % metrics.precision(2.0))
    print("Recall for positive: %.3f" % metrics.recall(2.0))
    

In [0]:
# Scores for normal random forest model
eval(predictions_rf)

% correct:  0.9302325581395349
Accuracy = 0.909091
Test Error = 0.0909091
F1 Score:  0.8658008658008657


In [0]:
# Confusion matrix, precision and recall for normal random forest model
confusion_matrix(predictions_rf)

/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(
Confusion Matrix:
[[  0.   0.  12.]
 [  0.   0.  16.]
 [  0.   0. 280.]]
Precision for negative: 0.000
Recall for negative: 0.000
Precision for neutral: 0.000
Recall for neutral: 0.000
Precision for positive: 0.909
Recall for positive: 1.000


In [0]:
# Scores for weighted random forest model
eval(predictions)

% correct:  0.7906976744186046
Accuracy = 0.748428
Test Error = 0.251572
F1 Score:  0.7754895949137162


In [0]:
# Confusion matrix, precision and recall for weighted random forest model
confusion_matrix(predictions)

/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(
Confusion Matrix:
[[  2.   2.  11.]
 [  1.   4.  16.]
 [  8.  42. 232.]]
Precision for negative: 0.182
Recall for negative: 0.133
Precision for neutral: 0.083
Recall for neutral: 0.190
Precision for positive: 0.896
Recall for positive: 0.823


#NAIVE BAYES TESTING.. CHECKING HOW GOOD OUR MODEL IS

In [0]:
from pyspark.ml.classification import NaiveBayes
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

nb = NaiveBayes(smoothing=1.0, modelType="multinomial", labelCol="labelled_sentiment", featuresCol="features")
nb_model = nb.fit(training)
prediction_nb = nb_model.transform(testing)
# evaluator_nb = MulticlassClassificationEvaluator(labelCol="labelled_sentiment", predictionCol="prediction", metricName="f1")
# f1_score = evaluator_nb.evaluate(prediction_nb)
# print(f1_score)

In [0]:
# Scores for Naive Bayes
eval(prediction_nb)

% correct:  0.9368770764119602
Accuracy = 0.886792
Test Error = 0.113208
F1 Score:  0.8335849056603775


In [0]:
# Confusion matrix, precision and recall for Naive Bayes
confusion_matrix(prediction_nb)

Confusion Matrix:
[[  0.   0.  15.]
 [  0.   0.  21.]
 [  0.   0. 282.]]
Precision for negative: 0.000
Recall for negative: 0.000
Precision for neutral: 0.000
Recall for neutral: 0.000
Precision for positive: 0.887
Recall for positive: 1.000


#LOGISTIC REGRESSION..CHECKING HOW GOOD OUR MODEL IS..
THIS WILL BE USED FOR RESEARCH REVIEWS

In [0]:
from pyspark.ml.classification import LogisticRegression
from pyspark.mllib.regression import LabeledPoint
from pyspark.mllib.classification import LogisticRegressionWithLBFGS
from pyspark.ml.linalg import Vector as MLVector, Vectors as MLVectors
from pyspark.mllib.linalg import Vector as MLLibVector, Vectors as MLLibVectors


In [0]:
training_rdd = training.rdd.map(lambda row: LabeledPoint(row['labelled_sentiment'], row['features'].toArray()))
lr_multiclass_model = LogisticRegressionWithLBFGS.train(training_rdd, numClasses=3)
testing_rdd = testing.rdd.map(lambda row: LabeledPoint(row['features'].toArray()))

In [0]:
@udf(returnType=IntegerType())
def lr_multi_predict(vec):
    return lr_multiclass_model.predict(MLLibVectors.fromML(vec))

In [0]:
tested = testing.withColumn("prediction", lr_multi_predict("features"))

In [0]:
tested = tested.withColumn("prediction", tested["prediction"].cast(DoubleType()))

In [0]:
eval(tested)

% correct:  0.8903654485049833
Accuracy = 0.842767
Test Error = 0.157233
F1 Score:  0.8409526544193855


In [0]:
confusion_matrix(tested)

/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(
Confusion Matrix:
[[  2.   8.   5.]
 [  2.   3.  16.]
 [  3.  16. 263.]]
Precision for negative: 0.286
Recall for negative: 0.133
Precision for neutral: 0.111
Recall for neutral: 0.143
Precision for positive: 0.926
Recall for positive: 0.933


In [0]:
display(tested)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text features weight prediction 1217318 6085380 2013 7353379 Ilaria Simone and I were in Martin's apartment for 6 days during our trip in the US. We didn't see much Martin because he was busy working, but the communication with him has always been excellent and Martin is kind and available. The location is very convenient to visit
 Manhattan, because the subway is 5 minutes walk. 
 The room was ok, however we are used to higher standards of
 cleanliness, mainly in the bathroom. 2 List(Simone, I, Martin, apartment, days, trip, US, We, see, much, Martin, busy, working, communication, always, excellent, Martin, kind, available, The, location, convenient, visit, Manhattan, subway, minutes, walk, The, room, ok, however, used, higher, standards, cleanliness, mainly, bathroom) Map(vectorType -> sparse, length -> 262144, indices -> List(329, 8538, 13020, 23097, 24698, 33960, 41660, 49707, 56781, 56998, 63746, 71450, 73341, 76764, 78745, 79132, 79779, 82515, 118174, 142239, 146982, 156204, 161061, 162250, 164686, 171078, 196815, 197185, 198197, 201496, 204971, 206426, 221843, 245086), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0)) 0.3762227238525207 1.0 1217318 8639549 2013 9194371 Ronan We had a great stay in Williamsburg with Martin and Roman. A nice room, great location, good facilities. Martin and Roman were very friendly, helpful and patient when we had any questions etc... We also got some good tips from them for things to do in the area - we recommend a stay! 2 List(We, great, stay, Williamsburg, Martin, Roman, A, nice, room, great, location, good, facilities, Martin, Roman, friendly, helpful, patient, questions, etc, We, also, got, good, tips, things, area, recommend, stay) Map(vectorType -> sparse, length -> 262144, indices -> List(22346, 33960, 68228, 73249, 73341, 83991, 113432, 130473, 132932, 145697, 146679, 147136, 162055, 164686, 165534, 174582, 207475, 214012, 214676, 221843, 225898, 228685, 261870), values -> List(1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 2.0)) 0.3762227238525207 2.0 3798941 17493706 2014 7755261 Guillaume We stayed in that room for a night and it was really nice. 
 The room is small, but it is furnished with a large and confy confy bed, and the room has a large closet. The temporary AC that was settled is very powerful, so that the room was cool. 
 
 The apartment is really nice and well decorated, especially the living room. 
 
 Thanks Martin for your good advice and for your communicative laughters! We really loved Traif, the tapas restaurant you told us about!! 2 List(We, stayed, room, night, really, nice, The, room, small, furnished, large, confy, confy, bed, room, large, closet, The, temporary, AC, settled, powerful, room, cool, The, apartment, really, nice, well, decorated, especially, living, room, Thanks, Martin, good, advice, communicative, laughters, We, really, loved, Traif, tapas, restaurant, told, us) Map(vectorType -> sparse, length -> 262144, indices -> List(13020, 21641, 22346, 30497, 33358, 33960, 37175, 43084, 52914, 55915, 65568, 71363, 79897, 86703, 96104, 109156, 113432, 148719, 155416, 163145, 164686, 171127, 174207, 186925, 189957, 195763, 201496, 216221, 220270, 221843, 223619, 224493, 224909, 229264, 251904), values -> List(1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 5.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 3.0, 1.0)) 0.3762227238525207 2.0 3798941 25132433 2015 11793338 Jonas We had a fantastic stay at Martin's apartment. He is a great guy and made us feel almost at home at his place. Our room was really nice with a comfy bed. The location is very convenient and Williamsburg (with all its great bars and restauran

# TRYING TFIDF WITH MULTICLASS LR

In [0]:
(training, testing) = tfidf.randomSplit([0.7, 0.3])

In [0]:
training_rdd = training_tfidf.rdd.map(lambda row: LabeledPoint(row['labelled_sentiment'], row['features'].toArray()))
lr_multiclass_model_tfidf = LogisticRegressionWithLBFGS.train(training_rdd, numClasses=3)
testing_rdd = testing_tfidf.rdd.map(lambda row: LabeledPoint(row['features'].toArray()))

In [0]:
@udf(returnType=IntegerType())
def lr_multi_predict_tfidf(vec):
    return lr_multiclass_model_tfidf.predict(MLLibVectors.fromML(vec))

In [0]:
tested_tfidf = testing.withColumn("prediction", lr_multi_predict_tfidf("features"))

In [0]:
display(tested_tfidf)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text features weight prediction 1217318 6085380 2013 7353379 Ilaria Simone and I were in Martin's apartment for 6 days during our trip in the US. We didn't see much Martin because he was busy working, but the communication with him has always been excellent and Martin is kind and available. The location is very convenient to visit
 Manhattan, because the subway is 5 minutes walk. 
 The room was ok, however we are used to higher standards of
 cleanliness, mainly in the bathroom. 2 List(Simone, I, Martin, apartment, days, trip, US, We, see, much, Martin, busy, working, communication, always, excellent, Martin, kind, available, The, location, convenient, visit, Manhattan, subway, minutes, walk, The, room, ok, however, used, higher, standards, cleanliness, mainly, bathroom) Map(vectorType -> sparse, length -> 262144, indices -> List(329, 8538, 13020, 23097, 24698, 33960, 41660, 49707, 56781, 56998, 63746, 71450, 73341, 76764, 78745, 79132, 79779, 82515, 118174, 142239, 146982, 156204, 161061, 162250, 164686, 171078, 196815, 197185, 198197, 201496, 204971, 206426, 221843, 245086), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0)) 0.3762227238525207 2 1217318 8639549 2013 9194371 Ronan We had a great stay in Williamsburg with Martin and Roman. A nice room, great location, good facilities. Martin and Roman were very friendly, helpful and patient when we had any questions etc... We also got some good tips from them for things to do in the area - we recommend a stay! 2 List(We, great, stay, Williamsburg, Martin, Roman, A, nice, room, great, location, good, facilities, Martin, Roman, friendly, helpful, patient, questions, etc, We, also, got, good, tips, things, area, recommend, stay) Map(vectorType -> sparse, length -> 262144, indices -> List(22346, 33960, 68228, 73249, 73341, 83991, 113432, 130473, 132932, 145697, 146679, 147136, 162055, 164686, 165534, 174582, 207475, 214012, 214676, 221843, 225898, 228685, 261870), values -> List(1.0, 2.0, 1.0, 2.0, 1.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 2.0)) 0.3762227238525207 2 3798941 17493706 2014 7755261 Guillaume We stayed in that room for a night and it was really nice. 
 The room is small, but it is furnished with a large and confy confy bed, and the room has a large closet. The temporary AC that was settled is very powerful, so that the room was cool. 
 
 The apartment is really nice and well decorated, especially the living room. 
 
 Thanks Martin for your good advice and for your communicative laughters! We really loved Traif, the tapas restaurant you told us about!! 2 List(We, stayed, room, night, really, nice, The, room, small, furnished, large, confy, confy, bed, room, large, closet, The, temporary, AC, settled, powerful, room, cool, The, apartment, really, nice, well, decorated, especially, living, room, Thanks, Martin, good, advice, communicative, laughters, We, really, loved, Traif, tapas, restaurant, told, us) Map(vectorType -> sparse, length -> 262144, indices -> List(13020, 21641, 22346, 30497, 33358, 33960, 37175, 43084, 52914, 55915, 65568, 71363, 79897, 86703, 96104, 109156, 113432, 148719, 155416, 163145, 164686, 171127, 174207, 186925, 189957, 195763, 201496, 216221, 220270, 221843, 223619, 224493, 224909, 229264, 251904), values -> List(1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 5.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 3.0, 1.0)) 0.3762227238525207 2 3798941 25132433 2015 11793338 Jonas We had a fantastic stay at Martin's apartment. He is a great guy and made us feel almost at home at his place. Our room was really nice with a comfy bed. The location is very convenient and Williamsburg (with all its great bars and restaurants) is

In [0]:
tested_tfidf = tested_tfidf.withColumn("prediction", tested_tfidf["prediction"].cast(DoubleType()))

In [0]:
eval(tested_tfidf)

% correct:  0.9716981132075472
Accuracy = 0.971698
Test Error = 0.0283019
F1 Score:  0.970558797328378


In [0]:
confusion_matrix(tested_tfidf)

Confusion Matrix:
[[ 11.   2.   2.]
 [  0.  17.   4.]
 [  0.   1. 281.]]
Precision for negative: 1.000
Recall for negative: 0.733
Precision for neutral: 0.850
Recall for neutral: 0.810
Precision for positive: 0.979
Recall for positive: 0.996


# Predict all data with MultiClass LR

In [0]:
df_processed_rdd = df_processed_with_hash.rdd.map(lambda row: LabeledPoint(row['features'].toArray()))

In [0]:
all_prediction_lr = df_processed_with_hash.withColumn("prediction", lr_multi_predict("features"))

In [0]:
wrong_prediction_lr = all_prediction_lr.filter(col("prediction") != col("labelled_sentiment"))

In [0]:
display(wrong_prediction_lr)

listing_id id date reviewer_id reviewer_name comments labelled_sentiment processed_text features prediction 44799007 666425016 2020 89762643 Diemeary I never post this detailed of a review but I feel this one is important to hit key points. This specific Airbnb is a great deal, great stay, amazing views, and very clean and nice. Although the Airbnb is attached to a partnering company Sonder, the Sonder process was not the same value as I am used to with Airbnb. You have to call the Sonder phone number directly and do everything practically outside of Airbnb. The check-in instructions never came but stated they would three days prior after completing the covid health questionnaire and sending confirmation which I did via email with a screenshot as requested, even after calling a day before stay to confirm the door access code downstairs and at the physical door upon check-in there was still a marked missed as no one had a clear answer as to where the codes to seem to be/how to retrieve them (odd) and to wait until the morning to receive final codes due to a "technical" issue that is "in process". Well, the morning came, and nothing was ever received but I was busy running around. I didn't freak out or anything like that because I was told a Sonder representative would be available on site. I arrive to the apartment style/hotel style location and the front security has no idea about check-ins and tells me she does not work with check-in and is with a third party company and knows nothing about Sonder staff on site. Of course this did not help my situation, so I called the Sonder number, again, to try to come to a resolution to get checked in, and the wait time was probably about 20 minutes until the same security calls me and points at a man who she says she believes is a supervisor on site with Sonder. All while this was happening, a man came in with a similar situation to mine. I flagged the representative down, and he helped me, if it hadn't been for him I would imagine waiting 30 minutes to an hour on the phone trying to figure the "technical" issue. He was unable to give a door code for either downstairs or my room but had the master key to at least let me in. This was a step in the right direction but still a headache having to call later to escalate my issue because I had a guest arriving later and I was not going to be at the stay at the time of their arrival so I needed to give the codes to enter the stay, the codes in which at that point I myself didn't even have. I will say Sonder did allow me to check-in early after it was approved but the whole check-in process was a blur and no one seemed to be on the same page which sucked because it ruined my first initial experience of an awesome stay. I would definitely say there is education and fixings needed in place to better fix issues like this between Sonder and Airbnb for the experience for the guest(s). The only other issue we had was our Wifi on and off working and this was only an issue primarily because the Wifi helped using the TV. The process in getting the Wifi also took about two days. It seems the turn around time to get a response is 24 hours writing Sonder on the Airbnb portal and hit or miss on the Sonder customer service line but who wants to spend all day on the phone on their trip. We eventually learned you can text Sonder as well. A contactless visit was scheduled, first representative couldn't fix the Wifi, second one fixed the Wifi. Heads up, TV Cast (C) is the app to download to sync videos, musics, and such to the tv. Cable is not included. All in all, after check-in, the stay was nice. Everything was clean and spacious and the washer and dryer worked great. Towels (extra as well), iron, ironing board, shampoo, conditioner, lotion, waters, chocolates, and hangers as well. There just needs to again be improvements because check-in to me is one of the most vital in the first impression of an Airbnb stay, but in this case it was more a Sonder stay, beca

#Using MultiClass LR to label our research paper data with our model

In [0]:
df_reviews = csv_to_df("reviews_original.csv")

In [0]:
df_reviews_count = csv_to_df("Hannahs_listing_ID.csv")

In [0]:
display(df_reviews_count)

listing_id count 26785 451 546383 424 550297 420 58059 407 467634 406 506121 405 5178 396 31994 396 476983 392 27024 389 63360 388 151199 359 51572 352 76761 351 106363 342 158955 339 92894 337 557018 336 27531 334 84659 331 126443 316 453094 311 54158 310 66340 310 24143 309 515408 308 545949 308 67208 306 94477 304 369831 302 26362 300 26969 297 479867 292 512210 280 115678 279 39704 275 531091 275 16580 274 231194 272 232612 272 276120 270 205043 267 483485 267 197753 266 300140 265 42580 262 64107 260 198786 258 15220 257 182177 255 45689 255 9783 252 270231 251 51485 251 229367 249 7322 248 75635 248 442636 247 347865 247 369411 246 404502 242 163814 242 199312 239 374548 238 328693 235 260765 235 518960 233 29628 233 501693 232 456190 231 135393 231 58101 231 175069 230 519310 229 12192 229 6990 229 211078 228 404923 227 107630 227 63657 227 113265 227 209310 223 243708 223 82638 222 9668 222 62095 221 320900 221 476919 220 206071 218 173151 216 282977 216 216015 216 498693 216 12937 214 30970 213 195123 213 55467 213 23135 213 3831 213 245504 211 481022 211 269889 211 33009 211 258284 209 246938 208 305211 208 230854 207 23545 207 64365 206 39267 206 83243 206 163627 205 227715 205 141154 205 182649 204 495249 204 12048 204 116940 202 411336 201 501098 200 470090 200 57297 199 161996 199 251262 199 278090 198 441860 197 311343 197 185478 195 50174 195 222913 195 324115 194 89621 193 360400 193 530431 192 286662 192 32023 192 256369 192 57874 191 44229 190 552519 190 84905 190 63320 189 320876 189 166006 188 16421 188 57468 188 11708 186 467866 185 197942 185 336220 184 9782 183 39282 183 33223 182 13552 182 501082 182 60611 182 292047 181 83811 181 57161 180 75193 180 419373 180 319724 179 271954 178 54860 178 64837 178

In [0]:
from pyspark.sql.types import BooleanType
@udf(returnType=BooleanType())
def check_if_english(text):
    try:
        language = detect(text)
    except:
        language = "error"
    return language == 'en'
def create_review_df_per_id(listing_id):
    reviews_by_id = df_reviews.filter(df_reviews['listing_id'] == listing_id)
    reviews_by_id = reviews_by_id.filter(check_if_english('comments'))
    return reviews_by_id.limit(20)

In [0]:
processed_reviews_df = df_reviews.limit(0)
display(processed_reviews_df)
review_rows = df_reviews_count.collect()
for row in review_rows:
    listing_id = row.listing_id
    id_reviews_df = create_review_df_per_id(listing_id)
    processed_reviews_df = processed_reviews_df.union(id_reviews_df)

listing_id id date reviewer_id reviewer_name comments

In [0]:
df_research_processed = processed_reviews_df.withColumn('processed_text', preprocess_text(processed_reviews_df['comments']))

In [0]:
hashTF = HashingTF(inputCol="processed_text", outputCol="features")
df_research_reviews_with_hash = hashTF.transform(df_research_processed)

In [0]:
df_research_reviews_prediction = df_research_reviews_with_hash.withColumn("prediction", lr_multi_predict("features"))

In [0]:
display(df_research_reviews_prediction)

listing_id id date reviewer_id reviewer_name comments processed_text features prediction 26785 51038 2010-06-08 116775 Mirm Superb host, courteous, really concerned about making sure everyone's comfortable, super responsive and pleasant List(Superb, host, courteous, really, concerned, making, sure, everyone, comfortable, super, responsive, pleasant) Map(vectorType -> sparse, length -> 262144, indices -> List(26855, 37101, 58339, 76570, 99892, 134125, 167918, 207672, 219137, 228905, 229264, 248069), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 2 26785 61298 2010-07-05 133432 Lisa Great little apartment in a great neighborhood. I told Dani that we'd be arriving at 7 a.m. and there was a note on the door so we would know we were in the right place. She was waiting for us. She lives downstairs and asked several times if we needed anything. Fortunately, we had no problems. 

The description didn't mention the fabulous claw-foot tub in the bathroom or the collection of menus provided so guests can acquaint themselves with the neighborhood's huge variety of dining options. 

The next time I visit New York, I will definitely look up Dani's place first. List(Great, little, apartment, great, neighborhood, I, told, Dani, arriving, note, door, would, know, right, place, She, waiting, us, She, lives, downstairs, asked, several, times, needed, anything, Fortunately, problems, The, description, mention, fabulous, tub, bathroom, collection, menus, provided, guests, acquaint, neighborhood, huge, variety, dining, options, The, next, time, I, visit, New, York, I, definitely, look, Dani, place, first) Map(vectorType -> sparse, length -> 262144, indices -> List(4959, 6346, 6498, 13020, 19719, 32550, 35407, 41660, 43157, 45190, 50202, 52914, 54961, 61901, 64489, 70076, 70998, 76526, 79697, 86311, 90859, 107810, 109156, 121517, 125808, 137477, 137855, 139371, 140931, 150080, 152481, 156204, 160852, 176950, 183547, 188835, 191184, 201496, 205538, 206426, 212953, 217158, 223763, 223953, 229166, 230188, 230862, 233903, 242022, 261870), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 2.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 2 26785 67528 2010-07-22 141032 Catherine Terrific place! Dani and her family are very hospitable, the area is lovely, and the apartment was perfect for us. The collection of menus was extensive - and very useful, and the kitchen is fully stocked with dishes, dry goods, coffee, pots and pans, etc. A window air conditioner and a floor-standing fan kept the place nice and cool, even during a heat wave. We'll definitely book the apartment for our next trip! List(Terrific, place, Dani, family, hospitable, area, lovely, apartment, perfect, us, The, collection, menus, extensive, useful, kitchen, fully, stocked, dishes, dry, goods, coffee, pots, pans, etc, A, window, air, conditioner, fan, kept, place, nice, cool, even, heat, wave, We, definitely, book, apartment, next, trip) Map(vectorType -> sparse, length -> 262144, indices -> List(6346, 13020, 13231, 22346, 25491, 52149, 54961, 56998, 59791, 70998, 79697, 80902, 83991, 87445, 98424, 109156, 110510, 144712, 144792, 145697, 148851, 159212, 159927, 162055, 167301, 168342, 169805, 174966, 189113, 190212, 191184, 201496, 207439, 212761, 212953, 218214, 221017, 221595, 221843, 223619, 247000), values -> List(1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 2 26785 73342 2010-08-03 140261 Gina My son and I enjoyed our stay in Dani's bright little apartment. We had the privacy and convenience of an apartment, but really felt like "guests" of Dani's due to her friendly helpfulness and the little amenities such as coffee beans for mor

In [0]:
prediction_count = df_research_reviews_prediction.groupby("prediction").count()
prediction_count.show()

+----------+-----+
|prediction|count|
+----------+-----+
|         2| 3055|
|         1|  238|
|         0|    7|
+----------+-----+



In [0]:
display(df_research_reviews_prediction)
df_research_reviews_prediction.printSchema()

In [0]:
df_research_reviews_prediction = df_research_reviews_prediction.groupBy('listing_id').agg(mean("mean_prediction"))

In [0]:
from pyspark.sql.types import IntegerType
from pyspark.sql.functions import udf

@udf(returnType=IntegerType())
def summarize_sentiment(sum):
    x = 0
    if sum >= 1.75:
        return 2
    elif sum < 1.75 and sum >= 1.5:
        return 1
    else:
        return 0

# df_listing_sentiment.withColumn("mean_prediction",df_listing_sentiment.mean_prediction.cast('int'))
df_listing_sentiment=df_research_reviews_prediction.withColumn('derived_summarize_sentiment',summarize_sentiment(df_research_reviews_prediction['mean_prediction']))
display(df_listing_sentiment)

In [0]:
pandas_df = df_listing_sentiment.toPandas()
pandas_df.to_csv("my_dataframe.csv", index=False)